In [1]:
import numpy as np
from scipy.linalg import eigh, eig, solve

In [2]:
import colorcet as cc
from bokeh.io import output_notebook, show
from bokeh.plotting import figure, ColumnDataSource
from bokeh.models import LinearColorMapper, ColorBar, CustomJS, Slider, Range1d, Span
from bokeh.layouts import column, gridplot
output_notebook()

Loading BokehJS ...

# General solution of coupled harmonic oscillators

Solve coupled harmonic oscillator equations defined by (positive definite) matrices $M$ and $K$ where
\begin{equation}
M \frac{\mathrm{d}^2\vec{q}}{\mathrm{d}t^2} + K \vec{q} = 0
\end{equation}
We simultaneously diagonalize the matrices $M$ and $K$ such that $A^T M A = \mathbb{1}$ and $A^T K A = \Omega^2$, where $\Omega$ is a diagonal matrix with entries $(\omega_1, \omega_2, \omega_3, \ldots,)$ on the diagonal, and the columns of $A$ are the eigenvectors $\vec{A}_\alpha$, i.e.,
\begin{gather}
K \vec{A}_\alpha = \omega_\alpha^2 M \vec{A}_\alpha,
\end{gather}
We note that this also implies that $A^{-1} = A^T M$, such that $A A^T M = \mathbb{1}$ as well (we know the inverse $A^{-1}$ exists because the generalized eigenproblem for positive definite matrices of size $N\times N$ always has $N$ independent eigenvectors).

This leads to a system of uncoupled equations for the normal coordinates $Q_\alpha$, with $\vec q = A \vec Q \Leftrightarrow \vec Q = A^T M \vec q$. This can be obtained from the original equation by replacing $\vec q \to A \vec Q$ and multiplying by $A^T$ from the left.
\begin{equation}
\frac{\mathrm{d}^2\vec Q}{\mathrm{d}t^2} + \Omega^2 \vec Q = 0 \quad\Leftrightarrow\quad \frac{\mathrm{d}^2 Q_\alpha}{\mathrm{d}t^2} + \omega_\alpha^2 Q_\alpha = 0,
\end{equation}
with solutions $Q_\alpha(t) = \operatorname{Re}\left[c_\alpha e^{-i\omega_\alpha t}\right]$, where $c_\alpha$ is a complex constant. We can obtain these coefficients as $c_\alpha = \vec{A}_\alpha^T M \left(\vec{q}(0) + \frac{i}{\omega_\alpha} \dot{\vec{q}}(0)\right)$.

Two side remarks:

1. if the original problem had been driven, $M \frac{\mathrm{d}^2\vec{q}}{\mathrm{d}t^2} + K \vec{q} = \vec f(t)$, the same procedure as above would lead to
\begin{equation}
\frac{\mathrm{d}^2\vec Q}{\mathrm{d}t^2} + \Omega^2 \vec Q = A^T \vec f(t) = \vec F(t) \quad\Leftrightarrow\quad \frac{\mathrm{d}^2 Q_\alpha}{\mathrm{d}t^2} + \omega_\alpha^2 Q_\alpha = F_\alpha(t)
\end{equation}
i.e., the normal modes are still independent, but driven by the forces transformed into the normal coordinate basis.

2. If there is damping, $M \frac{\mathrm{d}^2\vec{q}}{\mathrm{d}t^2} + C \frac{\mathrm{d}\vec{q}}{\mathrm{d}t} + K \vec{q} = \vec f(t)$, one has to solve a [quadratic eigenvalue problem](https://en.wikipedia.org/wiki/Quadratic_eigenvalue_problem), but the procedure is otherwise similar. In principle, this can be done by calculating the zeros of the characteristic polynomial, $\det(M \lambda^2 + C \lambda + K) = 0$. However, for numerical implementation, it is advantageous to use numerical eigensystem solvers, which can be done by linearizing the problem, i.e., transforming the quadratic problem to a linear one in a larger vector space. This can be done in various ways (see section 3.4 in http://eprints.ma.man.ac.uk/466/1/38198.pdf). We use a standard version, which gives
\begin{gather}
   \begin{pmatrix} 0 & \mathbb{1}\\ -K & -C \end{pmatrix} \vec{z} = \lambda \begin{pmatrix} \mathbb{1} & 0\\ 0 & M \end{pmatrix} \vec{z}
\end{gather}
where the $2N$ vectors $\vec{z}$ are $\begin{pmatrix} \vec{A} \\ \lambda \vec{A}\end{pmatrix}$. Note that while this can be verified to solve the quadratic eigenvalue problem, it can also be interpreted as the linear generalized eigenvalue problem that is obtained by rewriting the second-order differential equation $M \frac{\mathrm{d}^2\vec{q}}{\mathrm{d}t^2} + C \frac{\mathrm{d}\vec{q}}{\mathrm{d}t} + K \vec{q} = \vec f(t)$ into first-order form by introducing $\vec{v} = \frac{\mathrm{d}\vec{q}}{\mathrm{d}t}$, which gives
\begin{gather}
  \frac{\mathrm{d}\vec{q}}{\mathrm{d}t} = \vec{v}\\
  M \frac{\mathrm{d}\vec{v}}{\mathrm{d}t} + C \vec{v} + K \vec{q} = \vec f(t)
\end{gather}
Rewriting this system in matrix form for the solution vector $\begin{pmatrix} \vec{q} \\ \vec{v} \end{pmatrix}$ and assuming exponential behavior $e^{\lambda t}$ for the homogeneous solution gives the linearized eigenvalue problem above. The driving term becomes $\begin{pmatrix} \vec{0} \\ \vec{f}(t) \end{pmatrix}$.

In [3]:
β = 1.5
K = np.array([[1,0],[0,1]])
C = β*np.array([[1,-1],[-1,1]])
M = np.array([[1,0],[0,1]])

N = K.shape[0]
In = np.eye(N)
Zn = np.zeros((N,N))
Lλ = np.block([[In,Zn],[Zn,M]])
Lc = np.block([[Zn,In],[-K,-C]])
λs, zAs1 = eig(Lc,Lλ)
print(λs.round(15))

[-2.61803399+0.j -0.        +1.j -0.        -1.j -0.38196601+0.j]


In [4]:
class coupled_harmosc:
    def __init__(self,M,K,C=None):
        N = K.shape[0]
        assert K.shape == (N,N)
        assert M.shape == K.shape
        self.N = N
        self.K = K
        self.M = M
        self.C = C
        if self.C is None:
            ωssq, As = eigh(K,M)
            assert np.allclose(As.T @ M @ As,np.eye(N))
            assert np.allclose(As.T @ K @ As,np.diag(ωssq))
            self.ωs = np.sqrt(ωssq)
            self.As = As
        else:
            In = np.eye(N)
            Zn = np.zeros((N,N))
            Lλ = np.block([[In,Zn],[Zn,M]])
            Lc = np.block([[Zn,In],[-K,-C]])
            # note that the linearized eigenvalue problem 
            # is not symmetric or Hermitian, so we have to
            # use eig, not eigh. Even for symmetric forms,
            # Lλ is not positive definite, so eigh cannot be used
            λs, zAs = eig(Lc,Lλ)
            self.λs = λs
            self.zAs = zAs
    def solve(self,q0,v0,t):
        if self.C is None:
            # q(t) = As (Rcs cos(ωs t) + Ics sin(ωs t))
            # v(t) = As ωs (-Rcs sin(ωs t) + Ics cos(ωs t))
            # q0 = As Rcs -> As^T M q0 = As^T M As Rcs = Rcs
            # v0 = As ωs Ics -> As^T M v0 = As^T M As ωs Ics = ωs Ics
            Rcs = self.As.T @ self.M @ q0
            Ics = (self.As.T @ self.M @ v0) / self.ωs
            self.cs = Rcs + 1j*Ics
            cst = self.cs[:,None]*np.exp(-1j*self.ωs[:,None]*t[None,:])
            self.Q = np.real(cst)
            self.V = self.ωs[:,None] * np.imag(cst)
            self.q = self.As @ self.Q
            self.v = self.As @ self.V
            self.t = t
        else:
            # z0 = [q0,v0]
            z0 = np.r_[q0,v0]
            # there are 2N coefficients cⱼ characterizing the solution,
            # zᵢ(t) = Σⱼ zAᵢⱼ cⱼ exp(λⱼt)
            # for the nonsymmetric eigenvalue problem, the right eigenvectors
            # are not orthonormal with respect to Lλ, so just directly solve
            # the linear system to obtain the vector c:
            # zⱼ(0) = Σⱼ zAᵢⱼ cⱼ -> z0 = zA c -> c = zA^-1 z0
            self.cs = solve(self.zAs,z0)
            # Z(t) = [Q(t),V(t)]
            self.Z = self.cs[:,None]*np.exp(self.λs[:,None]*t[None,:])
            self.z = self.zAs @ self.Z
            # these should be real, check (up to 13 digits)
            assert np.all(np.isclose(self.z.imag,0),)
            self.z = self.z.real
            # z(t) = [q(t), v(t)]
            self.q = self.z[:self.N,:]
            self.v = self.z[self.N:,:]
            self.t = t

## Two coupled oscillators

In [5]:
k = 1.
kp = 0.85
K = np.array([[k+kp,-kp],[-kp,k+kp]])
M = np.array([[1.,0.],[0.,1]])
ch = coupled_harmosc(M,K)

t = np.linspace(0,30,501)
v0 = [0.,0.]
for q0 in ([1.,1.], [1.,-1.], [2.,0]):
    ch.solve(q0,v0,t)
    figs = [figure(width=500,height=110+40*ii) for ii in range(2)]
    for (ii,fig) in enumerate(figs):
        fig.line(ch.t,ch.q[ii,:])
        fig.yaxis.axis_label = "q" + "₁₂"[ii]
    figs[0].xaxis.major_label_text_font_size = '0pt'
    figs[1].xaxis.axis_label = "t"
    show(gridplot(figs,ncols=1))

### with friction
We get a symmetric mode without friction, and an asymmetric mode with friction

In [6]:
k = 1.
kp = 0.85
β = 0.1
K = np.array([[k+kp,-kp],[-kp,k+kp]])
M = np.array([[1.,0.],[0.,1]])
C = β*np.array([[1,-1],[-1,1]])

ch = coupled_harmosc(M,K,C)

t = np.linspace(0,30,501)
v0 = [0.,0.]
for q0 in ([1.,1.], [1.,-1.], [2.,0]):
    ch.solve(q0,v0,t)
    figs = [figure(width=500,height=110+40*ii) for ii in range(2)]
    for (ii,fig) in enumerate(figs):
        fig.line(ch.t,ch.q[ii,:])
        fig.yaxis.axis_label = "q" + "₁₂"[ii]
    figs[0].xaxis.major_label_text_font_size = '0pt'
    figs[1].xaxis.axis_label = "t"
    show(gridplot(figs,ncols=1))

## Chain of coupled oscillators

In [7]:
N = 40
xs = np.linspace(-1,1,N)
ms = np.ones(N)
ωs = np.ones(N)
gs = (-.5 * ms * ωs**2)[1:]
M = np.diag(ms)
K = np.diag(ms*ωs**2)
for ii in range(N-1):
    K[ii,ii+1] = K[ii+1,ii] = gs[ii]
ch = coupled_harmosc(M,K)

In [8]:
q0 = np.exp(-xs**2/(2*0.15**2))
v0 = np.zeros_like(q0)
t = np.linspace(0.,200.,2001)
ch.solve(q0,v0,t)

In [9]:
fig = figure(width=600,plot_height=300)
cm = LinearColorMapper(palette=cc.coolwarm)
fig.image(image=[ch.q],x=ch.t[0],y=0,dw=ch.t[-1]-ch.t[0],dh=N,color_mapper=cm,level="image")
fig.xaxis.axis_label = "t"
fig.yaxis.axis_label = "oscillator number i"
fig.x_range.range_padding = fig.y_range.range_padding = 0
fig.add_layout(ColorBar(color_mapper=cm), 'right')
fig.xgrid.visible = fig.ygrid.visible = False
show(fig)

In [10]:
source = ColumnDataSource(data=dict(x=range(1,N+1),y=ch.q[:,0],ys=list(ch.q)))

fig = figure(width=600,height=300)
fig.circle('x','y',source=source,size=6)
fig.line('x','y',source=source)
fig.xaxis.axis_label = "oscillator number i"
fig.yaxis.axis_label = "qᵢ"
fig.y_range = Range1d(-1.05,1.05)

slider = Slider(start=0, end=len(t)-1, value=0, step=1, title="time step")
callback = CustomJS(args=dict(source=source, slider=slider),
                    code="""const it = slider.value, y = source.data['y'], ys = source.data['ys'];
                            for (var i = 0; i < y.length; i++) { y[i] = ys[i][it] }
                            source.change.emit();""")
slider.js_on_change('value', callback)
show(column(slider,fig))

In [11]:
fig = figure(width=600,height=300)
fig.circle(range(1,N+1),abs(ch.cs)**2,size=6)
fig.xaxis.axis_label = "Normal mode number α"
fig.yaxis.axis_label = "|cₐ|²"
show(fig)

In [12]:
fig = figure(width=600,height=300)
fig.circle(range(1,N+1),0.5*ch.ωs**2*abs(ch.cs)**2,size=6)
fig.xaxis.axis_label = "Normal mode number α"
fig.yaxis.axis_label = "Normal mode energy Eₐ"
show(fig)

In [13]:
takeinds, = np.where(abs(ch.cs)>0.04)
slider = Slider(start=0, end=len(t)-1, value=0, step=1, title="time step")

figs = []
callbacks = []
for ii in takeinds:
    nm = np.real(ch.cs[ii,None] * ch.As[:,None,ii] * np.exp(-1j*ch.ωs[ii,None]*t[None,:]))
    source = ColumnDataSource(data=dict(x=range(1,N+1),y=nm[:,0],ys=list(nm)))
    fig = figure(width=300,height=120)
    fig.circle('x','y',source=source,size=6)
    fig.line('x','y',source=source)
    fig.y_range = Range1d(-0.4,0.4)
    callback = CustomJS(args=dict(source=source, slider=slider),
                        code="""const it = slider.value, y = source.data['y'], ys = source.data['ys'];
                                for (var i = 0; i < y.length; i++) { y[i] = ys[i][it] }
                                source.change.emit();""")
    callbacks.append(callback)
    figs.append(fig)

slider.js_on_change('value', *callbacks)
show(column(slider,gridplot(figs,ncols=3)))

## Oscillator coupled to a "bath"

We here treat a "main" oscillator ($q_0$) coupled to a "continuous bath" of oscillators with frequencies distributed over a wide range, i.e.,
\begin{gather}
\ddot q_0 + \omega_1^2 q_0 + \sum_{j=1}^N g_j q_j = 0\\
\ddot q_j + \omega_j^2 q_j + g_j q_0 = 0
\end{gather}
where $\omega_j = j \Delta\omega$ for $j=1,\ldots,N$, and  $g_j = \sqrt{\frac{2\kappa \omega_j}{\pi \omega_1}}$.

In [14]:
ω1 = 1.
T = 2*np.pi / ω1
κ = 1/(20*T) # decay over 20 oscillation cycles

Ns = (100, 300, 500)
ts = np.linspace(0.,300*T,6001)
chΔωs = []
for N in Ns:
    M = np.eye(N+1)
    K = np.zeros((N+1,N+1))
    K[0,0] = M[0,0]*ω1**2
    ωbs, Δω = np.linspace(0,2*ω1,N+1,retstep=True)
    ωbs = ωbs[1:]
    for i,ω in enumerate(ωbs,start=1):
        # k = m ω^2
        K[i,i] = M[i,i]*ω**2
        K[0,i] = K[i,0] = np.sqrt(2*κ*Δω/np.pi*ω/ω1)

    ch = coupled_harmosc(M,K)

    q0 = np.zeros(N+1); q0[0] = 1.
    v0 = np.zeros(N+1)
    ch.solve(q0,v0,ts)
    
    chΔωs.append((ch,Δω))

The oscillation can be described (approximately) by the **complex** frequency $\omega_{\mathrm{eff}} = \omega_1 - \frac{i}{2} \kappa$ (corresponding to oscillation with frequency $\omega_1$ and decay of the amplitude with rate $\kappa/2$ (energy is quadratic in amplitude and thus decays with rate $\kappa$).

In [15]:
ωeff = ω1-0.5j*κ

fig = figure(width=600,height=300)
fig.line(ch.t/T,ch.q[0,:],color="black",line_width=2)
fig.line(ch.t/T,np.exp(-1j*ωeff*ch.t).real,color='orange',line_width=2,line_dash=[6,4]);
fig.xaxis.axis_label = "t / T"
fig.yaxis.axis_label = "q₁"
fig.x_range = Range1d(0,20)
show(fig)

The "discretization" of the bath with different numbers of modes $N$ leads to recurrence, i.e., energy coming back to the "main" oscillator. The recurrence happens at time $1/\Delta\omega$ (with $\Delta\omega$ the energy spacing between bath modes). For a continuous bath ($N\to\infty$, $\Delta\omega\to0$), it goes to infinity.

In [16]:
fig = figure(width=600,height=300)
for N,(ch,Δω),color in zip(Ns,chΔωs,('blue','orange','green')):
    fig.line(ch.t/T,ω1**2*ch.q[0,:]**2 + ch.v[0,:]**2, legend_label=f"N = {N}",color=color,line_width=2)
    fig.renderers.append(Span(location=1/Δω,dimension='height',line_color=color,line_width=2,line_dash=[6,4]))
fig.line(ch.t/T,np.exp(-κ*ch.t),color='black',line_width=2,line_dash=[6,4], legend_label=r"exp(-κt)")
fig.xaxis.axis_label = "t / T"
fig.yaxis.axis_label = "Energy of oscillator 1"
show(fig)